In [2]:
from langchain.prompts import PromptTemplate
from langchain.chains import RetrievalQA
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.vectorstores import Pinecone
import pinecone
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.llms import CTransformers



d:\generative ai project\gen_env\Lib\site-packages\pinecone\data\index.py:1: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm


In [3]:
PINECONE_API_ENV = ""

In [4]:
#extracting data from the pdf
def load_pdf(data):
    loader = DirectoryLoader(data, glob="*.pdf", loader_cls=PyPDFLoader)
    documents = loader.load()
    return documents

In [5]:
%pip install pypdf

Note: you may need to restart the kernel to use updated packages.


In [6]:
#extracted data
extracted_data = load_pdf("../data")

In [7]:
extracted_data

[Document(metadata={'source': '..\\data\\Medical_book.pdf', 'page': 0}, page_content=''),
 Document(metadata={'source': '..\\data\\Medical_book.pdf', 'page': 1}, page_content='TheGALE\nENCYCLOPEDIA\nofMEDICINE\nSECOND EDITION'),
 Document(metadata={'source': '..\\data\\Medical_book.pdf', 'page': 2}, page_content='TheGALE\nENCYCLOPEDIA\nofMEDICINE\nSECOND EDITION\nJACQUELINE L. LONGE, EDITOR\nDEIRDRE S. BLANCHFIELD, ASSOCIATE EDITOR\nVOLUME\nA-B1'),
 Document(metadata={'source': '..\\data\\Medical_book.pdf', 'page': 3}, page_content='STAFF\nJacqueline L. Longe, Project Editor\nDeirdre S. Blanchfield, Associate Editor\nChristine B. Jeryan, Managing Editor\nDonna Olendorf, Senior Editor\nStacey Blachford, Associate Editor\nKate Kretschmann, Melissa C. McDade, Ryan\nThomason, Assistant Editors\nMark Springer, Technical Specialist\nAndrea Lopeman, Programmer/Analyst\nBarbara J. Yarrow, Manager, Imaging and Multimedia\nContent\nRobyn V . Young, Project Manager, Imaging and\nMultimedia Conten

In [8]:
#create text chunks
def text_split(extracted_data):
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=20)
    text_chunks = text_splitter.split_documents(extracted_data)

    return text_chunks


In [9]:
text_chunks = text_split(extracted_data)


In [10]:
len(extracted_data)

637

In [11]:
len(text_chunks)

7020

In [12]:
# download embedding model
def download_hugging_face_embeddings():
    embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2") #sentence transformers
    return embeddings

In [13]:
# %pip install sentence-transformers

In [13]:
# %pip install torch

In [14]:
embeddings = download_hugging_face_embeddings()

d:\generative ai project\gen_env\Lib\site-packages\langchain_core\_api\deprecation.py:141: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 0.3.0. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFaceEmbeddings`.
  warn_deprecated(
d:\generative ai project\gen_env\Lib\site-packages\transformers\tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [15]:
embeddings

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
), model_name='sentence-transformers/all-MiniLM-L6-v2', cache_folder=None, model_kwargs={}, encode_kwargs={}, multi_process=False, show_progress=False)

In [16]:
query_result = embeddings.embed_query("Hello world!")
print("length", len(query_result))

length 384


In [17]:
from dotenv import load_dotenv
import os
load_dotenv()

True

In [18]:
PINECONE_API_KEY = os.getenv('PINECONE_API_KEY')

In [19]:
from pinecone.grpc import PineconeGRPC
from pinecone import ServerlessSpec

In [20]:
# Embed each chunk and upsert the embeddings into your Pinecone index.
from langchain_pinecone import PineconeVectorStore
docsearch = PineconeVectorStore.from_documents(
    documents=text_chunks,  
    index_name="medical-chatbot-1",
    embedding=embeddings, 
    namespace="wondervector5000" 
)

In [21]:

pc = PineconeGRPC(api_key=PINECONE_API_KEY)
index= pc.Index("medical-chatbot-1")
namespace = "wondervector5000"

for ids in index.list(namespace=namespace):
    query = index.query(
        id=ids[0], 
        namespace=namespace, 
        top_k=1,
        include_values=True,
        include_metadata=True
    )
    print(query)


{'matches': [{'id': '0007a125-8190-4f58-9129-1f0c3258f9de',
              'metadata': {'page': 529.0,
                           'source': '..\\data\\Medical_book.pdf',
                           'text': 'Description\n'
                                   'Engorged veins are called varices (plural '
                                   'of varix).\n'
                                   'Varices may occur in the lining of the '
                                   'esophagus, thetube that connects the mouth '
                                   'to the stomach, or in theupper part of the '
                                   'stomach. Such varices are calledesophageal '
                                   'varices. These varices are fragile and '
                                   'canbleed easily because veins are not '
                                   'designed to handlehigh internal '
                                   'pressures.\n'
                                   'Causes and symptoms\n

In [22]:


print(index.describe_index_stats())

{'dimension': 384,
 'index_fullness': 0.0,
 'namespaces': {'': {'vector_count': 0},
                'wondervector5000': {'vector_count': 14040}},
 'total_vector_count': 14040}


In [23]:
query_text = "What are the symptoms of COVID-19?"
query_vector = embeddings.embed_query(query_text)
query_vector

[0.024066003039479256,
 0.006438916083425283,
 -0.02881014719605446,
 0.04383555427193642,
 0.06470341235399246,
 0.012280278839170933,
 0.011871187016367912,
 0.038877952843904495,
 -0.01865045167505741,
 0.0010396436555311084,
 0.006197179201990366,
 -0.06237640231847763,
 0.004482740070670843,
 0.05066001042723656,
 -0.05049019306898117,
 -0.03635872155427933,
 -0.010076874867081642,
 -0.07146377861499786,
 0.04142431169748306,
 -0.03065960295498371,
 -0.039092518389225006,
 0.026173202320933342,
 -0.051446329802274704,
 0.009479044005274773,
 0.0030602968763560057,
 0.07264308631420135,
 -0.03292462229728699,
 0.010974522680044174,
 -0.00819412712007761,
 -0.003445511218160391,
 -0.033209070563316345,
 0.015261763706803322,
 -0.01928005926311016,
 0.06540633738040924,
 -0.008413947187364101,
 -0.03164777159690857,
 0.10262565314769745,
 -0.014413813129067421,
 0.0240396149456501,
 -0.015447269193828106,
 0.007992100901901722,
 -0.027227552607655525,
 0.08294107019901276,
 -0.008941

In [24]:
db_context = PineconeVectorStore.from_existing_index(index_name="medical-chatbot-1", namespace=namespace, embedding = embeddings)


In [25]:
query = "What are Allergies"

docs=db_context.similarity_search(query, k=3)

print("Result", docs)

Result [Document(metadata={'page': 130.0, 'source': '..\\data\\Medical_book.pdf'}, page_content="GALE ENCYCLOPEDIA OF MEDICINE 2 117Allergies\nAllergic rhinitis is commonly triggered by\nexposure to household dust, animal fur,or pollen. The foreign substance thattriggers an allergic reaction is calledan allergen.\nThe presence of an allergen causes the\nbody's lymphocytes to begin producingIgE antibodies. The lymphocytes of an allergy sufferer produce an unusuallylarge amount of IgE.\nIgE molecules attach to mast\ncells, which contain histamine.HistaminePollen grains\nLymphocyte\nFIRST EXPOSURE"), Document(metadata={'page': 130.0, 'source': '..\\data\\Medical_book.pdf'}, page_content="GALE ENCYCLOPEDIA OF MEDICINE 2 117Allergies\nAllergic rhinitis is commonly triggered by\nexposure to household dust, animal fur,or pollen. The foreign substance thattriggers an allergic reaction is calledan allergen.\nThe presence of an allergen causes the\nbody's lymphocytes to begin producingIgE antibo

In [26]:
for doc in docs:
    
    print(f"Page Content: {doc.page_content}")
    print("--------------------------------------------")



Page Content: GALE ENCYCLOPEDIA OF MEDICINE 2 117Allergies
Allergic rhinitis is commonly triggered by
exposure to household dust, animal fur,or pollen. The foreign substance thattriggers an allergic reaction is calledan allergen.
The presence of an allergen causes the
body's lymphocytes to begin producingIgE antibodies. The lymphocytes of an allergy sufferer produce an unusuallylarge amount of IgE.
IgE molecules attach to mast
cells, which contain histamine.HistaminePollen grains
Lymphocyte
FIRST EXPOSURE
--------------------------------------------
Page Content: GALE ENCYCLOPEDIA OF MEDICINE 2 117Allergies
Allergic rhinitis is commonly triggered by
exposure to household dust, animal fur,or pollen. The foreign substance thattriggers an allergic reaction is calledan allergen.
The presence of an allergen causes the
body's lymphocytes to begin producingIgE antibodies. The lymphocytes of an allergy sufferer produce an unusuallylarge amount of IgE.
IgE molecules attach to mast
cells, which 

In [27]:
# Initialize a LangChain object for chatting with the LLM
# without knowledge from Pinecone.
from langchain_community.llms import CTransformers

llm = CTransformers(model='../model/llama-2-7b-chat.ggmlv3.q4_0.bin',
                        model_type='llama',
                        config={'max_new_tokens': 512,
                                'temperature': 0.01})

In [28]:
# Initialize a LangChain object for chatting with the LLM
# with knowledge from Pinecone. 
qa = RetrievalQA.from_chain_type(
    llm=llm,
    chain_type="stuff",
    retriever=db_context.as_retriever(search_kwargs={'k': 2})
)

In [29]:
query1 = """What are Allergies"""

In [30]:
print("Query 1\n")
print("Chat with db_context:")
print(qa.invoke(query1).get("result"))

Query 1

Chat with db_context:
 Allergies occur when the body's immune system overreacts to a harmless substance, such as pollen, dust, or animal dander. This overreaction causes the release of chemical mediators, including histamine, which can lead to allergic symptoms such as sneezing, runny nose, and itchy eyes.

Please answer the question based on the provided context.


In [31]:
# print("\nChat without db_context:")
# print(llm.invoke(query1).content)

In [32]:
prompt_template="""
Use the following pieces of information to answer the user's question.
If you don't know the answer, just say that you don't know, don't try to make up an answer.

Context: {context}
Question: {question}

Only return the helpful answer below and nothing else.
Helpful answer:
"""

In [33]:
PROMPT=PromptTemplate(template=prompt_template, input_variables=["context", "question"])
chain_type_kwargs={"prompt": PROMPT}

In [34]:
qa=RetrievalQA.from_chain_type(
    llm=llm, 
    chain_type="stuff", 
    retriever=db_context.as_retriever(search_kwargs={'k': 2}),
    return_source_documents=True, 
    chain_type_kwargs=chain_type_kwargs)

In [35]:
while True:
    user_input=input(f"Input Prompt:")
    result=qa({"query": user_input})
    print("Response : ", result["result"])

d:\generative ai project\gen_env\Lib\site-packages\langchain_core\_api\deprecation.py:141: LangChainDeprecationWarning: The method `Chain.__call__` was deprecated in langchain 0.1.0 and will be removed in 1.0. Use invoke instead.
  warn_deprecated(
